# Alpha Regressor
The purpose of this notebook is to see whether we can regress a value for the student's overall skill level, using a record of their experience (X) and mastery (U) working against simulated questions.

Results 2018-10-01:
No, we can't.


In [190]:
from collections import defaultdict
from copy import copy
from math import exp, sqrt
from random import random, shuffle, choice, randint, uniform

from keras import Input, Model
from keras.callbacks import EarlyStopping
from keras.constraints import non_neg, max_norm
import numpy
from numpy import array, mean, ones
from pandas import concat
from pandas import DataFrame
from keras.models import Sequential
from keras.layers import LSTM, multiply, subtract, add, Activation, Lambda, division
from keras.layers import Dense, concatenate, MaxPooling1D, LocallyConnected1D, Reshape
from keras import backend as K
from keras import constraints

from utils import generate_student_name
import random

nq = 30
n_traits = 5
tr_len = 100
tt_len = 10


In [2]:
generate_student_name()

'KOOVYH THUSSA '

In [3]:
class Question():
    def __init__(self, qix, nt=10):
        #self.MAX_BETA = 15
        self.id = qix
        self.qvals = [ int(uniform(0,1)>=0.5) for _ in range(nt) ]
        #self.betas= [ (qval*randint(1,self.MAX_BETA)) for qval in qvals ]
        #print("Made q with betas:", self.betas)

random.seed(666)
qs = [Question(qix, n_traits) for qix in range(10)]
for q in qs:
    print(q.id, q.qvals)

0 [0, 1, 0, 1, 1]
1 [1, 1, 0, 1, 0]
2 [1, 1, 1, 0, 1]
3 [0, 1, 0, 1, 1]
4 [0, 1, 1, 0, 1]
5 [0, 1, 0, 1, 1]
6 [0, 1, 1, 0, 0]
7 [1, 0, 0, 0, 0]
8 [0, 1, 1, 1, 1]
9 [1, 1, 1, 0, 1]


In [191]:
def generate_learning_rates(nt=10):
    gammas = [uniform(0.1,1) for _ in range(nt)]
    betas= [ randint(1,10) for _ in range(nt) ]
    return betas, gammas

In [5]:
def generate_student_struct(nt=10, nq=20):
    name = generate_student_name()
    alpha = randint(1,10)
    h_practice = [ 0 for _ in range(nt) ]
    o_practice = [ 0 for _ in range(nq) ]
    mastery = [0 for _ in range(nq)]
    
    dict = {}
    dict["name"] = name
    dict["alpha"] = alpha
    dict["h_practice"] = h_practice
    dict["o_practice"] = o_practice
    dict["mastery"] = mastery
    return dict

In [76]:
def attempt_q(student, q: Question, betas, gammas):
    a = student["alpha"]
    Ts = student["h_practice"]
    p = calculate_pass_probability(betas, gammas, a, Ts, q.qvals)
    this_att = uniform(0,1)
    if (this_att <= p):
        passed=True
        student["mastery"][q.id] = 1
    else:
        passed=False

    student["o_practice"][q.id] += 1 
    
    for trix, qv in enumerate(q.qvals):
        if qv==1:
            student["h_practice"][trix] += 1
    return passed

In [79]:
def calculate_pass_probability(betas, gammas, a, Ts, qvals):
    # additive factors model is:
    # p_pass = 1 / 1 + exp(-z)
    # where z = a + sum[1:n]( -b + gT )
 
    phi_components = [ ((g*T)-b) for b,g,T,qv in zip(betas,gammas,Ts,qvals) if qv==1]
    print("calc/ing pass: alpha={}, sum_comps={}".format(a,sum(phi_components)))
    phi = sum(phi_components)
    z = a + phi
    print("z={}".format(z))
    try:
        p_pass = 1.0 / (1.0 + exp(-z))
        print("p_pass={}".format(p_pass))
    except OverflowError:
        p_pass = 0.0
    #print("real p_pass = {}".format(p_pass))
    return p_pass
    

In [192]:
def pass_predictor(nq):
    x = Input(shape=(nq,), name="in_x")
    u = Input(shape=(nq,), name="in_u")
    hidden = concatenate([x,u])
#     hidden = Dense(int(1.2*nq), activation="relu")(hidden)
#     hidden = Dense(int(0.7*nq), activation="relu")(hidden)
    alpha_est = Dense(1, activation="sigmoid")(hidden)
    model = Model(inputs=[x,u], outputs=[alpha_est])
    model.compile(optimizer='adam', loss="binary_crossentropy", metrics=["acc"])
    return model

def alpha_regressor(nq, nt):
    x = Input(shape=(nq,), name="in_x")
    u = Input(shape=(nq,), name="in_u")
    xsum = Lambda(lambda v : K.sum(v, axis=1, keepdims=True), name="xsum")(x)
    usum = Lambda(lambda v : K.sum(v, axis=1, keepdims=True), name="usum")(u)
#     rat = Input(shape=(1,), name="in_rat")
    hidden = concatenate([x,u, xsum,usum])    
    hidden = Dense(nq, activation="relu")(hidden)
#     hidden = Dense(nq, activation="relu")(hidden)
    hidden = Dense(nt, activation="relu")(hidden)
#     hidden = Dense(nt, activation="relu")(hidden)
    alpha_est = Dense(1, activation="relu")(hidden)
    model = Model(inputs=[x,u], outputs=[alpha_est])
    model.compile(optimizer='adam', loss="mse")
    return model



In [193]:
betas, gammas = generate_learning_rates(n_traits)
print("betas=",betas)
print("gammas=",gammas)

master_qs = [Question(qix, n_traits) for qix in range(nq)]
for q in master_qs:
    nocomps = sum(q.qvals)
    mag = sqrt(sum([ qmxv*pow(b, 2) for qmxv,b in zip(q.qvals,betas) ])) 
    print("Q:{}, difficulty={:.2f} across {} components".format(q.id, mag, nocomps))

betas= [7, 7, 10, 5, 8]
gammas= [0.5136005818813738, 0.7062227406373757, 0.8040734161197869, 0.8657156317455804, 0.9556897590756754]
Q:0, difficulty=10.00 across 1 components
Q:1, difficulty=16.19 across 4 components
Q:2, difficulty=11.75 across 3 components
Q:3, difficulty=15.43 across 4 components
Q:4, difficulty=10.63 across 2 components
Q:5, difficulty=16.19 across 4 components
Q:6, difficulty=11.75 across 3 components
Q:7, difficulty=12.21 across 2 components
Q:8, difficulty=11.75 across 3 components
Q:9, difficulty=5.00 across 1 components
Q:10, difficulty=10.63 across 2 components
Q:11, difficulty=12.81 across 2 components
Q:12, difficulty=9.90 across 2 components
Q:13, difficulty=11.75 across 3 components
Q:14, difficulty=7.00 across 1 components
Q:15, difficulty=11.18 across 2 components
Q:16, difficulty=11.09 across 3 components
Q:17, difficulty=16.19 across 4 components
Q:18, difficulty=9.43 across 2 components
Q:19, difficulty=9.43 across 2 components
Q:20, difficulty=11.09

# Training
This is where sh!t gets real.  We take our tr_len (1000?) students, and iterate over them 100 times to create 100,000 *complete examples* of a student attacking the curriculum.  The questions themselves are attacked in random order: the student has no intelligent guidance throught the material. (Obvious we may wish to provide that guidance at some point in the future.)

Remember, there are only 12 exercises in the curriculum, so if the student is taking 60 or 70 goes to answer them all, that's pretty poor.  But some of these kids are dumb as lumber, so cut them some slack!  They will all get there in the end since by the CMU AFM practice will, eventually, make perfect!

In [194]:
Xs = {}
Tz = {}
ys = {}
alphas = {}
psi_list = []
no_tr_students = 1000
for _ in range(no_tr_students):
    psi = generate_student_struct(n_traits, nq)
#     print(psi)
    psi_list.append(psi)

for run in range(1):
    print("----{}\n".format(run))
    for psi in psi_list:
        ct = 0
        psi["h_practice"] = [0 for _ in range(n_traits)]
        psi["o_practice"] = [0 for _ in range(nq)]
        psi["mastery"] = [0 for _ in range(nq)]
        qs = copy(master_qs)
        while(True):
            q = random.choice(qs)
            qix = q.id
            if qix not in Xs:
                Xs[qix]=[]
                Tz[qix]=[]
                ys[qix]=[]
                alphas[qix]=[]

            pre_question_profile = (tuple(psi["o_practice"]), tuple(psi["mastery"]))
#             print("PQP {} {}: {}".format(psi["name"], qix, pre_question_profile))
            Xs[qix].append( pre_question_profile )
            Tz[qix].append(tuple(psi["h_practice"]))
            
            #print("attempting {}".format(q.id))
            passed = attempt_q(psi, q, betas, gammas)
            ys[qix].append((1.0 if passed else 0.0))
            alphas[qix].append(psi["alpha"])

            ct+=1
            if passed:
                #print("passed")
                qs.remove(q)

            if qs == []:
                break
        print("{} ({}): curriculum completed in {} attempts".format(psi["name"], psi["alpha"], ct))

----0

calc/ing pass: alpha=4, sum_comps=-32.0
z=-28.0
p_pass=6.914400106935423e-13
calc/ing pass: alpha=4, sum_comps=-18.33808750028695
z=-14.33808750028695
p_pass=5.929901234724107e-07
calc/ing pass: alpha=4, sum_comps=-16.709304268221693
z=-12.709304268221693
p_pass=3.0228595881791875e-06
calc/ing pass: alpha=4, sum_comps=-25.889210661615692
z=-21.889210661615692
p_pass=3.116280888913915e-10
calc/ing pass: alpha=4, sum_comps=-13.2731849458483
z=-9.2731849458483
p_pass=9.390012407661115e-05
calc/ing pass: alpha=4, sum_comps=-7.445809700206137
z=-3.445809700206137
p_pass=0.030894069056709564
calc/ing pass: alpha=4, sum_comps=-20.443638248068638
z=-16.443638248068638
p_pass=7.221353665808994e-08
calc/ing pass: alpha=4, sum_comps=-17.46405175035443
z=-13.464051750354429
p_pass=1.4211371862055406e-06
calc/ing pass: alpha=4, sum_comps=-7.194660646768877
z=-3.1946606467688774
p_pass=0.039367147241721454
calc/ing pass: alpha=4, sum_comps=-5.22856819518203
z=-1.2285681951820298
p_pass=0.2264

p_pass=0.9999940778965912
calc/ing pass: alpha=3, sum_comps=4.376080547333
z=7.376080547333
p_pass=0.9993743418368713
calc/ing pass: alpha=3, sum_comps=7.086797882582503
z=10.086797882582502
p_pass=0.9999583762444666
calc/ing pass: alpha=3, sum_comps=4.233395158264621
z=7.233395158264621
p_pass=0.9992784558306705
calc/ing pass: alpha=3, sum_comps=11.074785401110676
z=14.074785401110676
p_pass=0.9999992283896736
calc/ing pass: alpha=3, sum_comps=-0.35111900656255735
z=2.6488809934374427
p_pass=0.9339419876386172
calc/ing pass: alpha=3, sum_comps=13.703252892262329
z=16.703252892262327
p_pass=0.9999999442981762
calc/ing pass: alpha=3, sum_comps=16.674328186156682
z=19.674328186156682
p_pass=0.999999997145383
calc/ing pass: alpha=3, sum_comps=23.540938683388365
z=26.540938683388365
p_pass=0.9999999999970255
calc/ing pass: alpha=3, sum_comps=12.845005073496864
z=15.845005073496864
p_pass=0.9999998685980913
calc/ing pass: alpha=3, sum_comps=22.08740598772348
z=25.08740598772348
p_pass=0.999

p_pass=0.9996162650455652
calc/ing pass: alpha=5, sum_comps=16.297186337292334
z=21.297186337292334
p_pass=0.9999999994366873
calc/ing pass: alpha=5, sum_comps=17.65011253277691
z=22.65011253277691
p_pass=0.9999999998543934
calc/ing pass: alpha=5, sum_comps=24.653719957491077
z=29.653719957491077
p_pass=0.9999999999998677
calc/ing pass: alpha=5, sum_comps=30.260737567821185
z=35.26073756782118
p_pass=0.9999999999999996
calc/ing pass: alpha=5, sum_comps=30.390269572017424
z=35.390269572017424
p_pass=0.9999999999999996
HIMIF DOB  (5): curriculum completed in 44 attempts
calc/ing pass: alpha=8, sum_comps=-20.0
z=-12.0
p_pass=6.144174602214718e-06
calc/ing pass: alpha=8, sum_comps=-30.53070965904295
z=-22.53070965904295
p_pass=1.640730009817297e-10
calc/ing pass: alpha=8, sum_comps=-27.55112316132874
z=-19.55112316132874
p_pass=3.2289037146337745e-09
calc/ing pass: alpha=8, sum_comps=-4.13428436825442
z=3.86571563174558
p_pass=0.9794818858671156
calc/ing pass: alpha=8, sum_comps=-13.524783

p_pass=0.9999986494150384
calc/ing pass: alpha=2, sum_comps=-5.175559503281279
z=-3.1755595032812787
p_pass=0.040095892135363013
calc/ing pass: alpha=2, sum_comps=-5.721879686466379
z=-3.7218796864663792
p_pass=0.023617194835397887
calc/ing pass: alpha=2, sum_comps=5.981237529429623
z=7.981237529429623
p_pass=0.9996583006452431
calc/ing pass: alpha=2, sum_comps=11.724163282065753
z=13.724163282065753
p_pass=0.9999989043517686
calc/ing pass: alpha=2, sum_comps=0.8938170625338859
z=2.893817062533886
p_pass=0.9475399445531556
calc/ing pass: alpha=2, sum_comps=13.899676363660179
z=15.899676363660179
p_pass=0.9999998755891558
calc/ing pass: alpha=2, sum_comps=7.124454812747514
z=9.124454812747514
p_pass=0.9998910437110502
calc/ing pass: alpha=2, sum_comps=18.641009568070622
z=20.641009568070622
p_pass=0.999999998914266
calc/ing pass: alpha=2, sum_comps=-1.1551924226823438
z=0.8448075773176562
p_pass=0.6994767802327254
calc/ing pass: alpha=2, sum_comps=0.35288972165805
z=2.35288972165805
p_p

z=24.070614986850998
p_pass=0.9999999999648226
calc/ing pass: alpha=5, sum_comps=17.162377604039946
z=22.162377604039946
p_pass=0.9999999997628617
calc/ing pass: alpha=5, sum_comps=22.9189058005214
z=27.9189058005214
p_pass=0.9999999999992502
calc/ing pass: alpha=5, sum_comps=9.087705379061907
z=14.087705379061907
p_pass=0.99999923829473
calc/ing pass: alpha=5, sum_comps=32.47462634341321
z=37.47462634341321
p_pass=1.0
calc/ing pass: alpha=5, sum_comps=27.48364241792425
z=32.48364241792425
p_pass=0.9999999999999922
calc/ing pass: alpha=5, sum_comps=19.235767019206435
z=24.235767019206435
p_pass=0.9999999999701779
calc/ing pass: alpha=5, sum_comps=14.055936417931237
z=19.055936417931235
p_pass=0.999999994702
calc/ing pass: alpha=5, sum_comps=8.191588623069562
z=13.191588623069562
p_pass=0.9999981337705308
calc/ing pass: alpha=5, sum_comps=35.35085237325963
z=40.35085237325963
p_pass=1.0
TOOPHOS LOSSI  (5): curriculum completed in 46 attempts
calc/ing pass: alpha=9, sum_comps=-7.0
z=2.0


...

p_pass=0.7039284542088242
calc/ing pass: alpha=9, sum_comps=-1.906781683768803
z=7.093218316231197
p_pass=0.9991699699814628
calc/ing pass: alpha=9, sum_comps=-5.917405513027309
z=3.082594486972691
p_pass=0.9561690478147361
calc/ing pass: alpha=9, sum_comps=0.7684501470111327
z=9.768450147011134
p_pass=0.9999427742951112
calc/ing pass: alpha=9, sum_comps=0.6287173736420035
z=9.628717373642004
p_pass=0.9999341929237016
calc/ing pass: alpha=9, sum_comps=1.1621937505275417
z=10.162193750527543
p_pass=0.9999613989991191
calc/ing pass: alpha=9, sum_comps=-5.175559503281279
z=3.8244404967187213
p_pass=0.9786357489773653
calc/ing pass: alpha=9, sum_comps=4.11203526417631
z=13.11203526417631
p_pass=0.999997979240819
calc/ing pass: alpha=9, sum_comps=2.915752009288169
z=11.91575200928817
p_pass=0.9999933157643602
calc/ing pass: alpha=9, sum_comps=3.5720964732790828
z=12.572096473279082
p_pass=0.999996532580639
calc/ing pass: alpha=9, sum_comps=0.19429379047348228
z=9.194293790473482
p_pass=0.99

p_pass=0.03255104573903625
calc/ing pass: alpha=5, sum_comps=-9.273238860858193
z=-4.273238860858193
p_pass=0.013745013005437654
calc/ing pass: alpha=5, sum_comps=-7.513967438176769
z=-2.5139674381767687
p_pass=0.07488479303368621
calc/ing pass: alpha=5, sum_comps=-10.665678869828799
z=-5.665678869828799
p_pass=0.0034508466082693074
calc/ing pass: alpha=5, sum_comps=-8.490165788234375
z=-3.490165788234375
p_pass=0.02959334277145895
calc/ing pass: alpha=5, sum_comps=-13.90243245828059
z=-8.90243245828059
p_pass=0.00013603906013423073
calc/ing pass: alpha=5, sum_comps=-0.2501622642512089
z=4.749837735748791
p_pass=0.9914211345953116
calc/ing pass: alpha=5, sum_comps=0.0622274063737569
z=5.062227406373757
p_pass=0.9937083938311393
calc/ing pass: alpha=5, sum_comps=-2.4772271253324734
z=2.5227728746675266
p_pass=0.9257229428458582
calc/ing pass: alpha=5, sum_comps=1.4746728876485076
z=6.474672887648508
p_pass=0.998460370850001
calc/ing pass: alpha=5, sum_comps=-4.001602875553891
z=0.998397

p_pass=0.9999999999771225
calc/ing pass: alpha=4, sum_comps=14.89940740102236
z=18.89940740102236
p_pass=0.9999999938042818
calc/ing pass: alpha=4, sum_comps=25.220147849908695
z=29.220147849908695
p_pass=0.9999999999997959
calc/ing pass: alpha=4, sum_comps=36.36093428867312
z=40.36093428867312
p_pass=1.0
calc/ing pass: alpha=4, sum_comps=33.92256784810269
z=37.92256784810269
p_pass=1.0
calc/ing pass: alpha=4, sum_comps=36.88122684580842
z=40.88122684580842
p_pass=1.0
calc/ing pass: alpha=4, sum_comps=12.068013997209142
z=16.068013997209142
p_pass=0.9999998948643172
calc/ing pass: alpha=4, sum_comps=10.603808871428923
z=14.603808871428923
p_pass=0.9999995453824524
calc/ing pass: alpha=4, sum_comps=15.892243976891887
z=19.892243976891887
p_pass=0.9999999977043366
THALL LESAPH  (4): curriculum completed in 48 attempts
calc/ing pass: alpha=9, sum_comps=-20.0
z=-11.0
p_pass=1.670142184809518e-05
calc/ing pass: alpha=9, sum_comps=-30.33808750028695
z=-21.33808750028695
p_pass=5.407373197059

p_pass=0.9035525912385413
calc/ing pass: alpha=5, sum_comps=-8.095637472409056
z=-3.095637472409056
p_pass=0.04328756403422794
calc/ing pass: alpha=5, sum_comps=-3.2215512046216226
z=1.7784487953783774
p_pass=0.8555052178617312
calc/ing pass: alpha=5, sum_comps=-13.447219485742634
z=-8.447219485742634
p_pass=0.0002144499974831245
calc/ing pass: alpha=5, sum_comps=-9.444096096892121
z=-4.444096096892121
p_pass=0.011611313572775521
calc/ing pass: alpha=5, sum_comps=-4.7202131023661
z=0.2797868976339002
p_pass=0.5694939782809659
calc/ing pass: alpha=5, sum_comps=-5.979632919401066
z=-0.979632919401066
p_pass=0.27296462654524895
calc/ing pass: alpha=5, sum_comps=-0.09796073054735732
z=4.902039269452643
p_pass=0.9926234055646731
calc/ing pass: alpha=5, sum_comps=-6.697096869538077
z=-1.6970968695380773
p_pass=0.15484481107436768
calc/ing pass: alpha=5, sum_comps=0.15708754679993486
z=5.157087546799935
p_pass=0.9942745233583002
calc/ing pass: alpha=5, sum_comps=-2.4976870493051155
z=2.502312

p_pass=0.9999999988429895
calc/ing pass: alpha=5, sum_comps=11.038166589996706
z=16.038166589996706
p_pass=0.9999998916789894
calc/ing pass: alpha=5, sum_comps=9.366951636511798
z=14.366951636511798
p_pass=0.9999994238813528
calc/ing pass: alpha=5, sum_comps=9.202415663362157
z=14.202415663362157
p_pass=0.9999993208449213
calc/ing pass: alpha=5, sum_comps=20.39298670311198
z=25.39298670311198
p_pass=0.999999999990625
calc/ing pass: alpha=5, sum_comps=7.635841382212119
z=12.635841382212119
p_pass=0.9999967467128289
calc/ing pass: alpha=5, sum_comps=12.845005073496864
z=17.845005073496864
p_pass=0.9999999822166835
calc/ing pass: alpha=5, sum_comps=22.05911441125329
z=27.05911441125329
p_pass=0.9999999999982283
calc/ing pass: alpha=5, sum_comps=20.658572754476552
z=25.658572754476552
p_pass=0.9999999999928118
calc/ing pass: alpha=5, sum_comps=7.83067755338489
z=12.83067755338489
p_pass=0.9999973226424288
calc/ing pass: alpha=5, sum_comps=3.6692480740363767
z=8.669248074036377
p_pass=0.999

In [195]:
for qix in Xs.keys():
    print("question",qix)
    x,u =zip(*Xs[qix])
    x = array(x)
    u = array(u)
    t = array(Tz[qix])
    y= array(ys[qix])
    a= array(alphas[qix])
    
    for ix in range(10):
#         print(x[ix,:], u[ix,:], t[ix,:], y[ix], ya[ix])
        print(x[ix,:], u[ix,:], y[ix], a[ix])
    print(x.shape)

question 1
[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0] [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0] 0.0 4
[0 1 1 1 1 1 1 0 0 1 0 1 2 2 0 1 1 3 1 2 1 0 0 1 1 1 1 1 1 2] [0 0 1 1 1 0 0 0 0 1 0 1 1 1 0 1 1 1 1 1 1 0 0 1 1 1 1 1 1 0] 1.0 4
[0 0 0 1 0 1 0 1 1 0 1 0 1 0 0 1 0 0 2 1 1 1 1 0 1 0 1 1 1 1] [0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 1 0 0 1 1 1 1 1 0 1 0 0 0 0 1] 1.0 8
[2 0 1 2 0 2 1 1 1 1 1 1 1 0 0 1 1 1 1 2 0 1 2 2 1 1 1 0 1 0] [1 0 0 1 0 1 1 1 1 1 1 1 1 0 0 1 1 1 1 1 0 1 1 1 1 1 0 0 0 0] 1.0 10
[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0] [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0] 0.0 8
[1 1 0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 1 0 0 0 0 0 0 0 0 0 0] [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0] 0.0 8
[2 2 1 2 1 2 0 0 1 1 1 1 1 1 0 1 2 1 2 1 1 1 1 1 1 1 1 0 1 2] [1 0 1 1 1 0 0 0 1 1 1 1 1 1 0 1 1 1 1 1 1 1 1 1 1 1 1 0 1 1] 1.0 8
[2 0 0 0 0 0 0 1 1 1 0 1 0 1 2 0 0 0 1 0 2 0 0 0 1 1 1 3 0 0] [0 0 0 0 0 0 0 0

[0 1 0 0 1 1 1 0 0 1 0 0 1 1 0 0 0 2 0 1 0 0 0 0 0 1 0 0 0 1] [0 0 0 0 1 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0] 1.0 4
[0 0 0 0 0 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 0] [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0] 0.0 8
[0 0 0 1 0 1 0 1 1 0 1 0 1 0 0 0 0 0 1 0 0 0 0 0 1 0 1 1 1 0] [0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0] 1.0 8
[2 0 1 2 0 1 1 0 0 0 1 0 0 0 0 0 1 0 0 2 0 0 2 1 1 0 1 0 1 0] [1 0 0 1 0 0 1 0 0 0 1 0 0 0 0 0 1 0 0 1 0 0 1 0 1 0 0 0 0 0] 1.0 10
[1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0] [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0] 0.0 8
[1 2 0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 1 0 0 0 0 0 0 0 0 0 0] [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0] 1.0 8
[0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 1 0 0 0 0 1 0 3 0 0] [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0] 0.0 4
[3 1 0 1 1 1 0 2 2 1 1 1 1 2 2 1 1 0 1 0 3 1 1 0 1 2 1 4 0 1] [1 0 0 1 1 1 0 1 1 1 1 0 1 

[2 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 1 1 1 0 1 0 0 0] [1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0] 0.0 10
[2 1 2 2 1 2 1 1 1 1 1 1 1 1 1 1 1 1 1 2 1 1 2 2 1 1 2 1 1 1] [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 1] 1.0 10
[1 2 1 1 0 2 0 0 0 0 1 1 0 0 0 0 1 0 2 1 0 0 0 0 0 1 0 0 0 1] [0 0 1 0 0 0 0 0 0 0 1 1 0 0 0 0 0 0 1 1 0 0 0 0 0 1 0 0 0 0] 1.0 8
[3 1 0 1 1 1 0 2 2 1 1 1 1 2 2 1 1 1 2 0 3 1 1 0 1 2 1 4 0 1] [1 0 0 1 1 1 0 1 1 1 1 0 1 1 1 1 1 1 1 0 1 1 0 0 1 1 0 1 0 1] 1.0 4
[1 1 0 1 0 3 1 1 1 1 2 1 1 2 1 3 2 3 1 3 1 1 2 0 2 2 0 0 0 3] [1 1 0 1 0 1 1 0 0 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 1 0 0 0 0] 1.0 3
[1 1 1 2 1 0 1 2 1 1 1 1 1 4 1 3 0 0 1 1 1 1 2 2 1 1 1 2 0 2] [1 1 1 1 1 0 1 1 1 1 1 1 1 1 1 1 0 0 1 1 0 1 1 1 1 1 1 1 0 1] 1.0 7
[0 1 1 0 1 0 1 1 2 0 1 1 1 0 1 0 1 0 1 1 1 0 1 0 0 1 1 2 0 1] [0 0 1 0 0 0 1 0 1 0 1 1 0 0 1 0 0 0 1 0 0 0 0 0 0 1 0 0 0 0] 1.0 6
(1419, 30)
question 3
[0 1 1 0 1 1 1 0 0 1 0 1 1 2 0 1 0 3 1 2 0 0 0 1 1 1 1 1 1 2] [0 0

In [196]:
passfail_models = [pass_predictor(nq) for _ in range(nq)]
alpha_model = alpha_regressor(nq, n_traits)
from keras.utils import plot_model
plot_model(passfail_model, to_file='cmu_passfail_model.png')
plot_model(alpha_model, to_file='cmu_alpha_model.png')
#passfail_model.summary()
alpha_model.summary()
input("go")

a_pds = []
for qix in Xs.keys():
    print("question",qix)
    pfm = passfail_models[qix]
    x,u = zip(*Xs[qix])
    x = array(x)
    u = array(u)
#     rat = numpy.sum(u, axis=1)/numpy.sum(x, axis=1)
    y = array(ys[qix])
    a = array(alphas[qix])
    es = EarlyStopping(monitor="loss", mode="auto")
    print("traiing pass fail model")
    pfm.fit([x,u],[y], verbose=0, epochs=100, shuffle=True, callbacks=[es])
    y_pds = list(pfm.predict([x,u]))

    score = pfm.evaluate([x,u], [y])
    print("pf score for", qix, "=", score)
# print("training alpha model")
# for ep in range(30):
    alpha_model.fit([x,u],[a], verbose=0, epochs=100, shuffle=True, callbacks=[es])
#     a_pds += list(alpha_model.predict([xs,us]))


    
# score = alpha_model.evaluate([xs,us], [tas])
# print("alpha score", score)
    
# for x,u,ta, pa in zip(xs,us,tas, a_pds):
#      print(x,u,ta,pa)

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
in_x (InputLayer)               (None, 30)           0                                            
__________________________________________________________________________________________________
in_u (InputLayer)               (None, 30)           0                                            
__________________________________________________________________________________________________
xsum (Lambda)                   (None, 1)            0           in_x[0][0]                       
__________________________________________________________________________________________________
usum (Lambda)                   (None, 1)            0           in_u[0][0]                       
__________________________________________________________________________________________________
concatenat

In [197]:
psi_alphas = defaultdict(list)
psi_y_hats = defaultdict(list)
psi_y_trues = defaultdict(list)

psi_test_list = []
for _ in range(10):
    psi = generate_student_struct()
    print(psi)
    psi_test_list.append(psi)

for psi in psi_test_list:
    psi_name = psi["name"]
    psi["h_practice"] = [0 for _ in range(n_traits)]
    psi["o_practice"] = [0 for _ in range(nq)]
    psi["mastery"] = [0 for _ in range(nq)]
    qs = copy(master_qs)
    ct=0
    while(True):
        q = random.choice(qs)
        qix = q.id
        print("chose q{}".format(qix))
        pfm = passfail_models[qix]

        x = array(psi["o_practice"]).reshape(1,-1)
        alpha = psi["alpha"]
        u = array(psi["mastery"]).reshape(1,-1)
        h = psi["h_practice"]
#         rat = numpy.sum(u, axis=1)/numpy.sum(x, axis=1)


        a_hat = alpha_model.predict([x,u])
        psi_alphas[psi_name].append(a_hat)
        y_hat = pfm.predict([x,u])
        psi_y_hats[psi_name].append(y_hat)
    
        #ytrue = calculate_pass_probability(betas, gammas, alpha, h, q.qvals)
        print("I think this guy has {}".format(a_hat))
        passed = attempt_q(psi, q, betas, gammas)

        ct += 1
        if passed:
            psi_y_trues[psi_name].append(1.0)
            qs.remove(q)
        else:
            psi_y_trues[psi_name].append(0)

        print("psi: {}, IQ: {}".format(psi["name"],psi["alpha"]))
        print("practice is now:", psi["o_practice"], psi["h_practice"])
        print("mastery is now:", psi["mastery"])

        if qs == []:
            print("complete")
            break
    print("curriculum completed in {} attempts".format(ct))


{'name': 'LES YIK ', 'alpha': 1, 'h_practice': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0], 'o_practice': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], 'mastery': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]}
{'name': 'MATH BALL ', 'alpha': 8, 'h_practice': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0], 'o_practice': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], 'mastery': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]}
{'name': 'SSALAB FOPH ', 'alpha': 6, 'h_practice': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0], 'o_practice': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], 'mastery': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]}
{'name': 'NUW DYSSE ', 'alpha': 2, 'h_practice': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0], 'o_practice': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], 'mastery': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]}
{'name': 'SSEV GOOT ', 'alpha': 5, 'h_practice': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0],

I think this guy has [[ 1.18199825]]
calc/ing pass: alpha=1, sum_comps=-1.1879120239860717
z=-0.18791202398607165
p_pass=0.45315974403434855
psi: LES YIK , IQ: 1
practice is now: [2, 0, 0, 2, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 0, 1, 0, 2, 0, 1, 1, 3, 0, 1, 0, 2, 2, 0, 1] [13, 15, 13, 10, 17]
mastery is now: [0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 1, 1, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0]
chose q25
I think this guy has [[ 1.18979144]]
calc/ing pass: alpha=1, sum_comps=8.246725904286482
z=9.246725904286482
p_pass=0.999903582450724
psi: LES YIK , IQ: 1
practice is now: [2, 0, 0, 2, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 0, 1, 0, 2, 0, 1, 1, 3, 0, 1, 1, 2, 2, 0, 1] [13, 15, 13, 10, 18]
mastery is now: [0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 1, 1, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0]
chose q0
I think this guy has [[ 1.42459953]]
calc/ing pass: alpha=1, sum_comps=0.4529544095572291
z=1.452954409557229
p_pass=0.8104527041047412
psi: LES YIK , IQ: 1
practice is now: [3, 0, 0, 2, 1, 1,

practice is now: [4, 1, 1, 3, 1, 2, 1, 2, 2, 1, 2, 2, 2, 1, 1, 1, 2, 1, 3, 1, 2, 1, 3, 1, 2, 1, 3, 2, 1, 2] [23, 28, 24, 19, 29]
mastery is now: [1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
chose q9
I think this guy has [[ 1.05263805]]
calc/ing pass: alpha=1, sum_comps=11.448597003166029
z=12.448597003166029
p_pass=0.9999960767922152
psi: LES YIK , IQ: 1
practice is now: [4, 1, 1, 3, 1, 2, 1, 2, 2, 2, 2, 2, 2, 1, 1, 1, 2, 1, 3, 1, 2, 1, 3, 1, 2, 1, 3, 2, 1, 2] [23, 28, 24, 20, 29]
mastery is now: [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
complete
curriculum completed in 53 attempts
chose q18
I think this guy has [[ 5.42923117]]
calc/ing pass: alpha=8, sum_comps=-13.0
z=-5.0
p_pass=0.0066928509242848554
psi: MATH BALL , IQ: 8
practice is now: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0] [0, 0, 0, 1, 1]
mastery is now: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

z=9.936523244361371
p_pass=0.9999516271386976
psi: MATH BALL , IQ: 8
practice is now: [0, 2, 2, 1, 1, 2, 1, 2, 0, 1, 0, 1, 1, 2, 1, 0, 1, 0, 1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 1, 1] [12, 13, 9, 11, 15]
mastery is now: [0, 1, 1, 1, 0, 0, 1, 0, 0, 1, 0, 1, 0, 1, 1, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0]
chose q21
I think this guy has [[ 6.71166611]]
calc/ing pass: alpha=8, sum_comps=7.679448996997501
z=15.6794489969975
p_pass=0.9999998449392952
psi: MATH BALL , IQ: 8
practice is now: [0, 2, 2, 1, 1, 2, 1, 2, 0, 1, 0, 1, 1, 2, 1, 0, 1, 0, 1, 1, 0, 1, 0, 0, 0, 1, 0, 0, 1, 1] [13, 14, 9, 11, 16]
mastery is now: [0, 1, 1, 1, 0, 0, 1, 0, 0, 1, 0, 1, 0, 1, 1, 0, 1, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0]
chose q22
I think this guy has [[ 6.66823912]]
calc/ing pass: alpha=8, sum_comps=-2.7633392549219185
z=5.2366607450780815
p_pass=0.9947101460376586
psi: MATH BALL , IQ: 8
practice is now: [0, 2, 2, 1, 1, 2, 1, 2, 0, 1, 0, 1, 1, 2, 1, 0, 1, 0, 1, 1, 0, 1, 1, 0, 0, 1, 0, 0, 1, 1] [13, 14, 10, 11

I think this guy has [[ 7.18626833]]
calc/ing pass: alpha=6, sum_comps=-15.560992350390018
z=-9.560992350390018
p_pass=7.041792077084262e-05
psi: SSALAB FOPH , IQ: 6
practice is now: [0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 0, 0, 0] [1, 2, 2, 2, 4]
mastery is now: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0]
chose q12
I think this guy has [[ 6.6537137]]
calc/ing pass: alpha=6, sum_comps=-12.073953936843875
z=-6.073953936843875
p_pass=0.0022967657433873873
psi: SSALAB FOPH , IQ: 6
practice is now: [0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 0, 0, 0] [2, 3, 2, 2, 4]
mastery is now: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0]
chose q27
I think this guy has [[ 6.58252573]]
calc/ing pass: alpha=6, sum_comps=-15.031371578022423
z=-9.031371578022423
p_pass=0.00011958404011421105
psi: SSALAB FOPH , IQ: 6
practice is now: [0,

...

I think this guy has [[ 0.60810912]]
calc/ing pass: alpha=1, sum_comps=16.32243450780028
z=17.32243450780028
p_pass=0.9999999700109805
psi: SOOTHET CHIH , IQ: 1
practice is now: [1, 1, 1, 1, 1, 1, 1, 1, 1, 3, 2, 2, 1, 0, 2, 2, 2, 2, 1, 1, 1, 2, 3, 1, 2, 1, 0, 0, 1, 2] [17, 21, 16, 15, 19]
mastery is now: [0, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 1, 1, 0, 1, 1, 0, 0, 0, 1, 1, 1, 0, 0, 1, 1, 0, 0, 1, 0]
chose q18
I think this guy has [[ 0.60810912]]
calc/ing pass: alpha=1, sum_comps=18.143839898621543
z=19.143839898621543
p_pass=0.9999999951478304
psi: SOOTHET CHIH , IQ: 1
practice is now: [1, 1, 1, 1, 1, 1, 1, 1, 1, 3, 2, 2, 1, 0, 2, 2, 2, 2, 2, 1, 1, 2, 3, 1, 2, 1, 0, 0, 1, 2] [17, 21, 16, 16, 20]
mastery is now: [0, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 1, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1, 0, 0, 1, 1, 0, 0, 1, 0]
chose q0
I think this guy has [[ 0.60810912]]
calc/ing pass: alpha=1, sum_comps=2.86517465791659
z=3.86517465791659
p_pass=0.9794710110300209
psi: SOOTHET CHIH , IQ: 1
practice is now: [2, 1, 1,

practice is now: [1, 1, 1, 0, 2, 0, 0, 0, 1, 0, 1, 3, 1, 2, 0, 1, 0, 1, 1, 1, 0, 1, 1, 3, 0, 1, 0, 1, 0, 1] [14, 10, 9, 7, 20]
mastery is now: [0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 1, 0, 0, 0, 1, 0, 1, 0, 1, 0, 0]
chose q3
I think this guy has [[ 1.96124017]]
calc/ing pass: alpha=1, sum_comps=9.472692755184411
z=10.472692755184411
p_pass=0.9999717020460225
psi: CHUNID JIVI , IQ: 1
practice is now: [1, 1, 1, 1, 2, 0, 0, 0, 1, 0, 1, 3, 1, 2, 0, 1, 0, 1, 1, 1, 0, 1, 1, 3, 0, 1, 0, 1, 0, 1] [14, 11, 10, 8, 21]
mastery is now: [0, 1, 0, 1, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 1, 0, 0, 0, 1, 0, 1, 0, 1, 0, 0]
chose q12
I think this guy has [[ 1.88866138]]
calc/ing pass: alpha=1, sum_comps=0.9588582933503664
z=1.9588582933503664
p_pass=0.8764093404632645
psi: CHUNID JIVI , IQ: 1
practice is now: [1, 1, 1, 1, 2, 0, 0, 0, 1, 0, 1, 3, 2, 2, 0, 1, 0, 1, 1, 1, 0, 1, 1, 3, 0, 1, 0, 1, 0, 1] [15, 12, 10, 8, 21]
mastery is now: [0, 1, 0, 1, 0, 0, 0, 0, 1, 0, 0, 1, 1, 0, 0,

I think this guy has [[ 2.29438257]]
calc/ing pass: alpha=1, sum_comps=23.57212663739051
z=24.57212663739051
p_pass=0.9999999999786959
psi: CHUNID JIVI , IQ: 1
practice is now: [2, 1, 2, 1, 3, 1, 1, 1, 1, 1, 2, 3, 2, 3, 1, 2, 1, 1, 1, 1, 1, 2, 3, 3, 1, 1, 1, 1, 1, 2] [24, 23, 18, 16, 29]
mastery is now: [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
complete
curriculum completed in 47 attempts
chose q2
I think this guy has [[ 5.42923117]]
calc/ing pass: alpha=8, sum_comps=-20.0
z=-12.0
p_pass=6.144174602214718e-06
psi: CHAPHU SYCHE , IQ: 8
practice is now: [0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0] [0, 1, 0, 1, 1]
mastery is now: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
chose q26
I think this guy has [[ 5.35821867]]
calc/ing pass: alpha=8, sum_comps=-23.33808750028695
z=-15.33808750028695
p_pass=2.181489570144424e-07
psi: CHAPHU SYCHE , IQ: 8
pra

I think this guy has [[ 5.42923117]]
calc/ing pass: alpha=5, sum_comps=-17.0
z=-12.0
p_pass=6.144174602214718e-06
psi: JULUJ CHEVUF , IQ: 5
practice is now: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1] [0, 1, 1, 0, 0]
mastery is now: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
chose q4
I think this guy has [[ 5.41358042]]
calc/ing pass: alpha=5, sum_comps=-15.0
z=-10.0
p_pass=4.5397868702434395e-05
psi: JULUJ CHEVUF , IQ: 5
practice is now: [0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1] [1, 1, 1, 0, 1]
mastery is now: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
chose q15
I think this guy has [[ 5.10397291]]
calc/ing pass: alpha=5, sum_comps=-14.195926583880214
z=-9.195926583880214
p_pass=0.0001014415253367778
psi: JULUJ CHEVUF , IQ: 5
practice is now: [0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0,

I think this guy has [[ 2.77470446]]
calc/ing pass: alpha=5, sum_comps=6.413704409592925
z=11.413704409592924
p_pass=0.9999889570180854
psi: JULUJ CHEVUF , IQ: 5
practice is now: [0, 0, 1, 1, 2, 0, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 0, 1, 2, 0, 0, 1, 1, 2, 2] [13, 16, 8, 11, 13]
mastery is now: [0, 0, 0, 1, 0, 0, 1, 0, 1, 1, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0]
chose q7
I think this guy has [[ 2.6604085]]
calc/ing pass: alpha=5, sum_comps=-3.8906051065838456
z=1.1093948934161544
p_pass=0.7520162836576659
psi: JULUJ CHEVUF , IQ: 5
practice is now: [0, 0, 1, 1, 2, 0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 0, 1, 2, 0, 0, 1, 1, 2, 2] [14, 16, 9, 11, 13]
mastery is now: [0, 0, 0, 1, 0, 0, 1, 0, 1, 1, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0]
chose q0
I think this guy has [[ 2.04055166]]
calc/ing pass: alpha=5, sum_comps=-2.7633392549219185
z=2.2366607450780815
p_pass=0.9034936912058528
psi: JULUJ CHEVUF , IQ: 5
practice is now: [1, 0,

In [198]:
for psi in psi_test_list:
    psi_name = psi["name"]
    real_alpha = psi["alpha"]
    print("Scores for {}, real alpha {}:".format(psi_name, real_alpha))
    print("alphas")
    for pr_alpha in psi_alphas[psi_name]:
        print(pr_alpha)
    
    print("ys")
    num_matches = sum([ int(yh>=0.5)==yt for yh, yt in zip(psi_y_hats[psi_name], psi_y_trues[psi_name])])
    print("match_list", match_list)
    score =  num_matches/len(psi_y_trues[psi_name])
    for y_hat, y_true in zip(psi_y_hats[psi_name], psi_y_trues[psi_name]):
        print(y_hat, y_true)
    print(score)

Scores for LES YIK , real alpha 1:
alphas
[[ 5.42923117]]
[[ 5.48290777]]
[[ 5.59618473]]
[[ 4.00569057]]
[[ 3.84000683]]
[[ 2.14488983]]
[[ 1.93500805]]
[[ 2.03004885]]
[[ 1.59387898]]
[[ 1.05524743]]
[[ 0.85979605]]
[[ 0.71693373]]
[[ 1.11849451]]
[[ 1.39737272]]
[[ 1.41770482]]
[[ 1.30375218]]
[[ 1.28179622]]
[[ 1.18124878]]
[[ 1.00492465]]
[[ 0.97992581]]
[[ 1.22960353]]
[[ 1.19287539]]
[[ 1.42197013]]
[[ 1.29257929]]
[[ 1.18176675]]
[[ 1.08909774]]
[[ 1.0641129]]
[[ 1.06475401]]
[[ 1.10705674]]
[[ 1.18199825]]
[[ 1.18979144]]
[[ 1.42459953]]
[[ 1.36249375]]
[[ 1.51408005]]
[[ 1.642892]]
[[ 1.60787773]]
[[ 1.58092737]]
[[ 1.44753754]]
[[ 1.45908844]]
[[ 1.52725673]]
[[ 1.32952237]]
[[ 1.43043244]]
[[ 1.37882662]]
[[ 1.3209697]]
[[ 1.32872653]]
[[ 1.30930638]]
[[ 1.15817499]]
[[ 0.98734891]]
[[ 0.97124994]]
[[ 0.91517889]]
[[ 1.00502801]]
[[ 0.89275277]]
[[ 1.05263805]]
ys
match_list [True, False, True, True, True, True, True, True, True, True, True, True]
[[ 0.11675201]] 0
[[ 0.175

[[ 0.99999654]] 1.0
[[ 0.99992752]] 1.0
[[ 1.]] 1.0
[[ 1.]] 1.0
[[ 1.]] 1.0
[[ 1.]] 1.0
[[ 1.]] 1.0
[[ 1.]] 1.0
0.9574468085106383
Scores for VON HUNUN , real alpha 3:
alphas
[[ 5.42923117]]
[[ 5.27930546]]
[[ 3.60193586]]
[[ 3.86514854]]
[[ 1.97557735]]
[[ 2.05818605]]
[[ 2.20885301]]
[[ 1.8952508]]
[[ 2.10631633]]
[[ 2.16521406]]
[[ 1.29419982]]
[[ 1.37613225]]
[[ 1.482759]]
[[ 1.74984646]]
[[ 1.71713316]]
[[ 1.84986734]]
[[ 1.70868683]]
[[ 1.56333923]]
[[ 1.69172955]]
[[ 1.59564447]]
[[ 1.43568325]]
[[ 1.73827553]]
[[ 1.72469878]]
[[ 1.77559626]]
[[ 1.88776588]]
[[ 1.79352295]]
[[ 1.79118276]]
[[ 1.72430301]]
[[ 2.01767206]]
[[ 1.83285248]]
[[ 1.89472818]]
[[ 1.78332531]]
[[ 1.67368042]]
[[ 1.59528065]]
[[ 1.60674906]]
[[ 1.70711756]]
[[ 1.57427061]]
[[ 1.55008149]]
[[ 1.69742465]]
[[ 1.62084246]]
[[ 1.44566822]]
[[ 1.55725241]]
[[ 1.65441382]]
[[ 1.72258151]]
[[ 1.85811841]]
[[ 1.66038394]]
[[ 1.39244986]]
[[ 1.30489898]]
[[ 1.24549866]]
ys
match_list [True, False, True, True, True

[[ 0.06416034]] 0
[[ 0.27051485]] 0
[[ 0.19984195]] 0
[[ 0.67047602]] 1.0
[[ 0.57034391]] 1.0
[[ 0.81701207]] 0
[[ 0.25154459]] 0
[[ 0.84894562]] 1.0
[[ 0.84351575]] 1.0
[[ 0.80460536]] 0
[[ 0.99506122]] 1.0
[[ 0.97485256]] 1.0
[[ 0.9835608]] 1.0
[[ 0.99976927]] 1.0
[[ 0.52996624]] 0
[[ 0.47333065]] 1.0
[[ 0.99973232]] 1.0
[[ 0.99997485]] 1.0
[[ 0.99985921]] 1.0
[[ 0.99807042]] 1.0
[[ 0.93656904]] 1.0
[[ 0.99999082]] 1.0
[[ 0.99959975]] 1.0
[[ 0.99992394]] 1.0
[[ 0.97126037]] 1.0
[[ 0.99999774]] 1.0
[[ 0.99999559]] 1.0
[[ 0.99999988]] 1.0
[[ 0.99999976]] 1.0
[[ 1.]] 1.0
[[ 1.]] 1.0
[[ 1.]] 1.0
[[ 1.]] 1.0
[[ 1.]] 1.0
[[ 1.]] 1.0
[[ 1.]] 1.0
0.9130434782608695


In [6]:
import os
duration = .5  # second
freq = 440  # Hz
os.system('play --no-show-progress --null --channels 1 synth %s sine %f' % (duration, freq))

0